Configuring ADLS Connectivity from Databricks

In [0]:
from pyspark.sql import SparkSession

# Initialize Spark Session
spark = SparkSession.builder \
    .appName("Delta Lake ETL") \
    .config("spark.sql.extensions", "io.delta.sql.DeltaSparkSessionExtension") \
    .config("spark.sql.catalog.spark_catalog", "org.apache.spark.sql.delta.catalog.DeltaCatalog") \
    .getOrCreate()

# Configure ADLS access
storage_account_name = "<azure_storage_account_name>"
storage_account_key = "<azure_storage_account_key>"
container_name = "<azure_container_name>"

spark.conf.set(f"fs.azure.account.key.{storage_account_name}.dfs.core.windows.net", storage_account_key)

In [0]:
# Define paths
adls_path = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net"
bronze_path = f"{adls_path}/bronze"
silver_path = f"{adls_path}/silver"
gold_path = f"{adls_path}/gold"

In [0]:
# Create database for Gold layer
spark.sql("CREATE DATABASE IF NOT EXISTS gold_db")
spark.sql("USE gold_db")

Out[8]: DataFrame[]

### CUSTOMER ANALYTICS TABLE
- For every customer fetch the first name, last name, phone, number of orders placed, lifetime value, average order total and additional info.

In [0]:
%sql
-- Fetch Schema of silver layer customers table.
-- Remember, data is residing in ADLS but exposed as a table in Databricks

DESCRIBE TABLE silver_db.silver_customers

col_name data_type comment customer_id string null first_name string null last_name string null email string null formatted_phone_number string null address string null city string null state string null zip_code string null country string null date_of_birth date null gender string null registration_date date null last_login timestamp null age decimal(18,6) null

In [0]:
%sql
DESCRIBE TABLE silver_db.silver_orders

col_name data_type comment order_id string null customer_id string null first_name string null last_name string null email string null promotion_id string null subtotal decimal(22,2) null shipping_cost decimal(11,2) null discount_amount decimal(34,2) null order_total_after_discount decimal(36,2) null num_items bigint null order_date timestamp null status string null payment_method string null shipping_address string null shipping_state string null shipping_city string null shipping_zip string null shipping_country string null

In [0]:
# Process Gold layer
spark.sql(f"""
                CREATE OR REPLACE TABLE gold_customer_analytics
                USING DELTA
                LOCATION '{gold_path}/customer_analytics'
                AS
                
                SELECT 
                    c.customer_id, c.first_name, c.last_name, c.formatted_phone_number,
                    COUNT(o.order_id) AS total_orders,
                    SUM(o.order_total_after_discount) AS lifetime_value,
                    AVG(o.order_total_after_discount) AS average_order_value,
                    
                    ROUND(DATEDIFF(MAX(o.order_date), MIN(o.order_date)) / COUNT(o.order_id), 2) AS average_days_between_orders
                
                FROM silver_db.silver_customers c
                LEFT JOIN silver_db.silver_orders o ON c.customer_id = o.customer_id
                GROUP BY c.customer_id, c.first_name, c.last_name, c.formatted_phone_number
""")

Out[14]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql

SELECT * FROM gold_db.gold_customer_analytics ORDER BY lifetime_value DESC

customer_id first_name last_name formatted_phone_number total_orders lifetime_value average_order_value average_days_between_orders 99f320f6-78fc-4c21-b8bc-8ea20957fd7e Kayla Mayer 330-865-7801 36 149267.28 4146.313333 1.22 24402009-a850-40af-ad0f-ff21ae1d0b05 Sean Lane 515-280-0384 42 131971.49 3142.178333 1.02 94b317f4-8d2d-40aa-af6d-712b0b067e69 Nicholas Brown 460-321-7789 38 130699.53 3439.461316 1.16 a364ac44-4b85-4dcf-bdf1-2b19018f12f9 Donald Cantrell 033-219-1815 44 129227.98 2936.999545 1.0 6027a1e8-3d3d-4c8c-9392-4e031aa6fefa Jeffery Gutierrez 473-934-2927 37 128138.20 3463.194595 1.19 68e5975b-631b-4c65-a746-2c809f45aa12 Kari Rogers 580-530-2269 40 127723.33 3193.083250 1.1 2fa15d1d-2a2a-4327-81df-7fbc980c9d06 John Williams 874-597-1299 46 126837.57 2757.338478 1.0 02080226-774e-421f-831e-669806329d28 Tracy Miller 812-499-8333 36 124383.73 3455.103611 1.28 6b057784-9181-4495-87a4-009b74bc98e8 Mary Montgomery 080-904-5255 36 122636.75 3406.576389 1.19 0404cb71-0c32-477c-af99-0b6533a7dc88 Cynthia Klein 271-487-3173 34 122589.94 3605.586471 1.32 f42923be-fb76-456f-ba0d-fe5df47c0c8a Matthew Garcia 516-845-5670 36 122231.48 3395.318889 1.31 9b4da956-bed4-4319-9589-9db5887cc2e0 Robert Hamilton 212-971-1739 36 119444.75 3317.909722 1.28 899ca0a1-838c-4d53-9799-cbdeea5d3858 Eric Holmes 596-949-8179 33 118415.08 3588.335758 1.39 5dd50970-e6f1-4ccb-a796-0619f0b4b81f Calvin Whitehead 254-118-7119 39 117611.00 3015.666667 1.18 d53451ed-4a3d-4a92-814c-cfe7e515114d Joshua Wilkinson 936-928-8418 35 117590.80 3359.737143 1.31 276dcec4-70c3-49e4-afc3-fe2d521c11f9 Wendy Reid 439-268-3329 34 117204.39 3447.187941 1.29 4b6d5801-c93a-4b9f-882d-9e141a9bdd99 Edward Gallegos 228-240-0294 33 116993.19 3545.248182 1.27 b8a903ce-729e-4a56-9d46-01e21fd773c2 Rick Riley 953-714-6519 35 116385.34 3325.295429 1.29 65bfb519-15d0-45b9-b57b-494d007e7cc6 Gregory Horton 829-901-3345 41 116315.81 2836.970976 1.1 63cb740d-a81c-4321-be0c-11da03c4d792 John Roberts 655-291-9941 33 116313.97 3524.665758 1.39 77b3e4aa-51b0-44dc-8073-6354197d62f6 Sean Riggs 851-285-9315 29 113989.10 3930.658621 1.59 0ab830ad-eb40-4e1a-963b-392bba7c817d Rachel Edwards 381-789-5847 32 113453.62 3545.425625 1.47 675d477c-fa2a-4346-b46c-546514fa18e4 Peggy Reed 319-838-2829 31 113185.60 3651.148387 1.45 1257bc95-9a20-429e-b11c-5c1ed84e524f Nathaniel Russell 209-163-5634 38 113048.88 2974.970526 1.16 7d2041aa-452e-4074-9374-7f5079304694 Craig Patton 931-625-0111 36 113021.60 3139.488889 1.14 947dd09b-7f05-43e6-b101-3ae1b8df9631 Ashley Bryant 578-937-2464 38 112845.26 2969.612105 1.16 31cfe145-7ec9-48f4-8f4c-a6df757a292d Jenna Schaefer 585-281-2815 28 112228.91 4008.175357 1.61 74b333bf-18c9-4dfd-b266-b80b87bb00d7 Virginia Ramsey 625-334-1238 38 111677.35 2938.877632 1.21 59de0c1a-bc28-4805-90bf-c55c8fd47608 Dana Garcia 508-525-5623 30 111221.57 3707.385667 1.53 4723d263-340e-44fe-b2cc-bcc610e70b5a Abigail Orozco 454-273-6223 33 110964.43 3362.558485 1.33 efaa375e-ba17-480b-b264-105b3abadaa4 Danielle Little 233-789-0662 37 110642.29 2990.332162 1.24 b45748d0-ed4c-4e53-9ff4-2f4245a1696f Tammie Freeman 542-311-3839 33 110443.08 3346.760000 1.33 1ae2dee9-0954-4461-915e-6601c802fb22 William Hogan 603-306-5294 31 110391.43 3561.013871 1.39 c35ae6bb-704e-4102-badc-5fabb1264c29 Matthew Ward 104-736-0523 38 110252.76 2901.388421 1.18 8581d0ef-a1db-45b2-835e-4cddb787165a Melissa Reynolds 825-363-2562 34 110108.58 3238.487647 1.35 e5b23ab5-37d0-4f5a-ab92-f7eed5c5f399 Tiffany Douglas 718-537-2237 25 109819.58 4392.783200 1.8 d773b3bc-9d77-4d37-b684-02003570359e Dean Molina 217-352-2821 40 109498.74 2737.468500 1.15 e6519ad2-9d88-4e07-a015-028505cf8fa2 Joshua Griffin 100-992-0496 29 109222.24 3766.284138 1.38 b88abd79-6478-4cb0-8a37-0bb3877ece99 Catherine Peck 138-576-5083 33 109044.08 3304.366061 1.42 f67e68e0-fd5a-4435-acfd-a272893f1cb2 James Lowe 099-903-5768 28 109000.08 3892.860000 1.64 9a7c915a-d7b4-4bec-820a-b2417d7f9f6c Donna Gonzalez 676-496-4946 28 108157.40 3862.764286 1.39 d5171462-43

### PRODUCT PERFORMANCE
- For every product, fetch the ID, name, category, price_category, number of orders containing this product, total quantity sold, total_revenue, average selling price

In [0]:
%sql
SELECT 
    p.product_id, p.product_name, p.category, p.price_category,
    COUNT(DISTINCT o.order_id) AS total_orders,
    SUM(oi.quantity) AS total_quantity_sold,
    SUM(oi.subtotal) AS total_revenue,
    AVG(oi.unit_price) AS average_selling_price

FROM silver_db.silver_products p
INNER JOIN silver_db.silver_orderLineItems oi ON p.product_id = oi.product_id
INNER JOIN silver_db.silver_orders o ON oi.order_id = o.order_id
GROUP BY p.product_id, p.product_name, p.category, p.price_category

product_id product_name category price_category total_orders total_quantity_sold total_revenue average_selling_price f97115fd-cd2b-4a27-aca6-4a77c32839f2 Reduced fresh-thinking knowledgebase Electronics Mid-range 8 37.0 2294.37 62.010000 6af6d5d1-b2a5-49be-b192-b3a917ff5b9e Integrated intermediate open architecture Sports Premium 6 21.0 6850.41 326.210000 c238d326-2293-426c-b970-c0b81fbe3d0d Universal clear-thinking attitude Pet Supplies Premium 4 26.0 5182.32 199.320000 6ec442ee-0bb4-487e-9fa3-445cdfbf520d Re-contextualized intangible collaboration Baby Products Premium 4 26.0 9344.92 359.420000 57fae15e-1937-4d48-9c65-c1c18b31f8f4 De-engineered responsive portal Uncategorized Premium 8 52.0 18719.48 359.990000 c6eb32d3-d95d-4e26-855b-3697ff6e93a8 Intuitive human-resource workforce Clothing Mid-range 8 46.0 3024.04 65.740000 e716139c-28b2-462d-9185-27a16cb41209 Progressive bandwidth-monitored process improvement Food & Beverages Premium 8 38.0 5375.86 141.470000 74c0ab81-e446-4962-beb8-e510ec154b58 Team-oriented well-modulated help-desk Uncategorized Premium 9 39.0 16679.91 427.690000 93bfd320-83a4-45d1-86d8-aa92ed4beb24 Re-contextualized global process improvement Movies Mid-range 6 27.0 1763.64 65.320000 880b9baf-fc81-4456-97ed-c4be70d62e3a Right-sized asynchronous pricing structure Automotive Premium 6 40.0 19310.40 482.760000 ab1a4860-673d-4d13-8181-65664ee98777 Secured systemic success Automotive Mid-range 4 33.0 2374.02 71.940000 3994a7bd-b3ae-4b79-a083-3c9d9e1a8c44 Team-oriented mission-critical moratorium Food & Beverages Premium 12 67.0 30826.70 460.100000 fced0cab-7e7b-46f9-8639-9ec3738db640 Synergistic impactful data-warehouse Sports Premium 7 19.0 3997.60 210.400000 a0664116-9db6-4733-98f7-ab439b316128 Synergized intermediate challenge Cosmetics Premium 8 36.0 10606.68 294.630000 7f792f3a-4118-4139-aff0-6f22e2a12d6e Enhanced methodical firmware Movies Premium 6 54.0 11813.58 218.770000 9d965f07-d411-4cde-88a2-2c59949fb02f Adaptive multi-state analyzer Outdoor & Camping Premium 7 34.0 8147.76 239.640000 28d9a180-ce17-4872-aa37-ca1525328af8 Ameliorated dynamic interface Baby Products Premium 7 28.0 10915.52 389.840000 ba6eed5a-bbec-43ea-99c1-d767fc26b96f Open-architected motivating emulation Cosmetics Premium 8 31.0 11433.73 368.830000 0f13c468-775e-4cda-b472-caec277b230f Open-source well-modulated methodology Outdoor & Camping Premium 3 21.0 3329.76 158.560000 81f53432-29f7-4582-b725-af3e9e0773ec De-engineered actuating portal Outdoor & Camping Premium 6 32.0 7331.52 229.110000 b017b48e-50ea-4914-9208-a52c4159a5f6 Synergized methodical framework Sports Premium 6 39.0 18677.49 478.910000 34798e76-0e15-4010-9c05-e12346c28867 Organized 5thgeneration complexity Uncategorized Premium 6 22.0 10806.18 491.190000 9569162f-352b-422a-80d9-d2b625d61167 Re-engineered clear-thinking Graphical User Interface Automotive Premium 7 41.0 17828.03 434.830000 0b36242b-2b79-4502-9259-c81ba7d10173 Adaptive next generation installation Furniture Premium 11 62.0 21287.08 343.340000 b06c9404-b23d-482f-8270-7ad08b2e3ecc Integrated systematic data-warehouse Jewelry Premium 8 34.0 5747.36 169.040000 c6330b39-8418-4de4-a9ec-f4bd2beb3f4b Function-based executive approach Books Premium 10 56.0 16486.96 294.410000 c17f9b62-743b-46c1-be61-ff96c22326b8 Upgradable asymmetric approach Outdoor & Camping Premium 5 39.0 17333.55 444.450000 3ad53696-e701-4c58-994a-50594ca9ab61 Mandatory motivating adapter Office Supplies Premium 6 39.0 13743.99 352.410000 98373b41-120a-4a77-8c04-f8e7d18d310c Intuitive grid-enabled interface Food & Beverages Mid-range 6 22.0 2075.48 94.340000 76621f71-f2b0-4354-8a26-35d140cf5c52 Streamlined content-based policy Books Premium 8 42.0 7548.66 179.730000 d1830e5f-6fef-4053-8292-d5d15e0a5c18 Decentralized motivating access Art & Crafts Mid-range 9 42.0 2499.42 59.510000 623e098a-fed1-4214-8dd1-4c57ab9530fb Future-proofed uniform archive Outdoor & Camping Mid-range 10 68.0 4889.20 71.900000 6419045d-318e-4cd9-bd2b-51326b36fd43 

In [0]:
spark.sql(f"""
                CREATE OR REPLACE TABLE gold_product_performance
                USING DELTA
                LOCATION '{gold_path}/product_performance'
                AS
                
                SELECT 
                    p.product_id, p.product_name, p.category, p.price_category,
                    COUNT(DISTINCT o.order_id) AS total_orders,
                    SUM(oi.quantity) AS total_quantity_sold,
                    SUM(oi.subtotal) AS total_revenue,
                    AVG(oi.unit_price) AS average_selling_price
                
                FROM silver_db.silver_products p
                INNER JOIN silver_db.silver_orderLineItems oi ON p.product_id = oi.product_id
                INNER JOIN silver_db.silver_orders o ON oi.order_id = o.order_id
                GROUP BY p.product_id, p.product_name, p.category, p.price_category
""")

Out[18]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql

SELECT * FROM gold_db.gold_product_performance ORDER BY total_revenue DESC LIMIT 10

product_id product_name category price_category total_orders total_quantity_sold total_revenue average_selling_price 63d36307-87c9-443a-9a23-47de410cdb54 Synergized composite neural-net Jewelry Premium 14 94.0 45334.32 482.280000 958c8a86-662a-4d25-90d6-1a92e797d9c3 Reactive executive toolset Art & Crafts Premium 11 89.0 43135.63 484.670000 1525c9a4-ab97-4df3-a32d-673e6c9bcf0e Ergonomic asymmetric budgetary management Jewelry Premium 14 85.0 42484.70 499.820000 dcf80aff-4927-451f-abca-8c37efb5ce1f Configurable user-facing toolset Office Supplies Premium 13 92.0 42021.00 456.750000 a6b82b49-ef9d-4524-801c-30d0d2eb4ecd Seamless solution-oriented success Home & Garden Premium 14 83.0 39571.08 476.760000 35355df2-ecea-4dfd-bd03-47a727c43649 Polarized modular migration Baby Products Premium 14 76.0 36964.88 486.380000 1b150399-f5eb-49f7-b479-765688ef5d8c Mandatory mobile interface Toys Premium 11 77.0 36179.99 469.870000 7385bfce-004f-46c2-8b78-6f7d869d19f8 Distributed solution-oriented architecture Food & Beverages Premium 14 77.0 36014.44 467.720000 a0a7e046-dec3-4d16-9ab1-0a0d99c09cca Cross-group object-oriented superstructure Home & Garden Premium 13 74.0 35706.48 482.520000 33e336c6-0739-485c-a041-c885d7ab5bb5 Team-oriented scalable hub Home & Garden Premium 15 75.0 35371.50 471.620000

### ORDER ANALYTICS
- On a given month, get the order statistics for each week day.

In [0]:
%sql

SELECT
    DATE_FORMAT(order_date, 'MMMM') AS month_name,
    DATE_FORMAT(order_date, 'EEEE') AS weekday_name,
    COUNT(*) AS total_orders,
    SUM(order_total_after_discount) AS total_revenue,
    ROUND(AVG(order_total_after_discount), 2) AS average_order_value,
    SUM(shipping_cost) AS total_shipping_cost
FROM silver_db.silver_orders
GROUP BY month_name, weekday_name

ORDER BY month_name, weekday_name

month_name weekday_name total_orders total_revenue average_order_value total_shipping_cost February Friday 1062 3023328.45 2846.83 29169.20 February Monday 1294 3674918.25 2839.97 35588.94 February Saturday 1633 4660716.02 2854.08 45313.23 February Sunday 1631 4622977.44 2834.44 44667.49 February Thursday 1094 3113826.05 2846.28 31568.33 February Tuesday 1113 3150578.27 2830.71 31236.74 February Wednesday 1100 2947895.22 2679.90 29820.63 January Friday 2774 7756003.50 2795.96 76109.80 January Monday 2238 6284281.93 2807.99 61389.74 January Saturday 2162 6092847.23 2818.15 58956.58 January Sunday 2195 6082370.12 2771.01 59272.94 January Thursday 2742 7739838.17 2822.70 76433.54 January Tuesday 2214 6252960.02 2824.28 60845.57 January Wednesday 2714 7407805.89 2729.48 75135.36

In [0]:
spark.sql(f"""
        CREATE OR REPLACE TABLE gold_order_analytics
        USING DELTA
        LOCATION '{gold_path}/order_analytics'
        AS
            SELECT
                DATE_FORMAT(order_date, 'MMMM') AS month_name,
                DATE_FORMAT(order_date, 'EEEE') AS weekday_name,
                COUNT(*) AS total_orders,
                SUM(order_total_after_discount) AS total_revenue,
                ROUND(AVG(order_total_after_discount), 2) AS average_order_value,
                SUM(shipping_cost) AS total_shipping_cost
            FROM silver_db.silver_orders
            GROUP BY month_name, weekday_name
            ORDER BY month_name, weekday_name
""")

Out[39]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

### PROMOTION EFFECTIVENESS
- How many orders got placed using given promotions?

- Total revenue generated using this promotion?

- For promotion duration, revenue generated for each day? 

In [0]:
spark.sql(f"""
                CREATE OR REPLACE TABLE gold_promotion_effectiveness
                USING DELTA
                LOCATION '{gold_path}/promotion_effectiveness'
                AS
                SELECT 
                    p.promotion_id, p.name AS promotion_name, p.discount_type, p.discount_value,
                    COUNT(DISTINCT o.order_id) AS total_orders,
                    SUM(o.order_total_after_discount) AS total_revenue,
                    AVG(o.order_total_after_discount) AS average_order_value,
                    SUM(o.order_total_after_discount) / NULLIF(DATEDIFF(p.end_date, p.start_date), 0) AS revenue_per_day
                FROM silver_db.silver_promotions p
                LEFT JOIN silver_db.silver_orders o
                ON p.promotion_id = o.promotion_id
                GROUP BY p.promotion_id, p.name, p.discount_type, p.discount_value, p.start_date, p.end_date
""")

Out[25]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql

SELECT * FROM gold_promotion_effectiveness ORDER BY total_revenue DESC

promotion_id promotion_name discount_type discount_value total_orders total_revenue average_order_value revenue_per_day ddc14a78-0065-461e-b8c7-cf70d58b61d9 Public-key solution-oriented alliance Fixed Amount 7.76 518 1851354.24 3574.042934 168304.930909 3901196c-1534-4faf-a775-daf5c913e794 Face-to-face value-added throughput Fixed Amount 10.20 529 1840759.98 3479.697505 368151.996000 a9064763-d11b-4f02-9e15-0d7e47019c92 Multi-tiered interactive framework Fixed Amount 10.00 530 1792633.90 3382.328113 199181.544444 bec1da03-5541-49fc-a3d6-f5c7ef7f667d Fundamental web-enabled process improvement Fixed Amount 20.56 540 1786708.10 3308.718704 77682.960870 4d4279d1-0b05-4225-8985-2314179f7e53 Total attitude-oriented software Fixed Amount 8.77 542 1777258.97 3279.075590 93539.945789 b56a339d-7819-4546-8a53-d22864e18472 Centralized object-oriented Graphic Interface Fixed Amount 27.03 539 1763035.38 3270.937625 103707.963529 31dd4d46-3c5e-4804-a006-00ef846cbe63 Proactive scalable orchestration Fixed Amount 23.79 547 1753006.35 3204.764808 64926.161111 5952a89e-26c0-44af-985e-2de13f35d83a Expanded non-volatile orchestration Fixed Amount 40.21 540 1734487.39 3212.013685 433621.847500 b23eb9c5-bb5f-43df-93ee-c3c8c87a640f Persevering tangible application Fixed Amount 35.52 535 1715691.82 3206.900598 65988.146923 5bbabf9b-0517-426a-970a-4f8b97147550 Secured systematic functionalities Percentage 5.00 541 1714867.64 3169.810795 131912.895385 4e6ece03-5728-4757-8f6d-7943106ae78e Balanced radical projection Fixed Amount 36.56 546 1711700.25 3134.982143 61132.151786 91527ba1-a6ac-48db-98c6-632573f3e4e0 Compatible object-oriented infrastructure Fixed Amount 32.26 514 1704264.20 3315.689105 189362.688889 3442db3f-c89b-4909-8d1f-63db334aa6d5 Polarized upward-trending core Fixed Amount 9.60 517 1698000.35 3284.333366 62888.901852 cf9f785c-afc9-400a-a324-ea355ddefab5 Advanced regional matrix Percentage 5.00 519 1694480.64 3264.895260 99675.331765 6dd403c1-83a3-48aa-99e3-1860ae8f2d6e Versatile modular methodology Fixed Amount 10.20 516 1692679.39 3280.386415 99569.375882 2fabef52-ebb1-43fb-8b82-98d6bd568812 Programmable impactful benchmark Fixed Amount 12.01 512 1689390.15 3299.590137 64976.544231 b242b07e-2bd5-4ffe-8d44-976e705a2457 Pre-emptive encompassing attitude Fixed Amount 42.69 514 1684806.96 3277.834553 null f54c9cd2-b787-4308-b68d-f2c23112e5ef Implemented user-facing capability Fixed Amount 46.93 508 1669060.93 3285.553012 79479.091905 1a47f448-b65a-4174-8e26-169525a39e45 Object-based full-range policy Fixed Amount 46.72 509 1661126.30 3263.509430 66445.052000 38fa7d12-a21d-4074-bed4-3048467c5d76 Ergonomic high-level algorithm Percentage 5.00 539 1658343.47 3076.704026 1658343.470000 d110bb1f-82fb-433d-a770-7e3b98180b75 Multi-tiered radical knowledgebase Fixed Amount 24.09 541 1651390.16 3052.477190 103211.885000 db8c69a8-1797-4830-a58c-2350b67c6341 Networked dynamic matrices Fixed Amount 42.73 487 1638469.98 3364.414743 91026.110000 e6cc04cd-77b6-4256-82f1-7dffd9b24533 Virtual cohesive model Fixed Amount 10.00 505 1630617.99 3228.946515 116472.713571 7312e020-459f-4918-9243-cb6f93619e10 Automated stable Graphical User Interface Fixed Amount 27.25 527 1629547.00 3092.119545 74070.318182 66183bab-d00c-460b-8e3b-a41aedfa8047 Multi-tiered attitude-oriented adapter Fixed Amount 43.75 497 1624729.53 3269.073501 101545.595625 a7990c87-f530-44d5-82b9-f59d725c0d03 De-engineered cohesive service-desk Fixed Amount 34.00 526 1624230.21 3087.890133 67676.258750 d12d18ff-4f90-4e1d-8784-c6e60054fda6 Reduced holistic complexity Fixed Amount 42.02 508 1602516.08 3154.559213 null 357c4195-8d4a-4aea-892b-25af030cc83f Extended client-driven attitude Fixed Amount 34.14 504 1564647.47 3104.459266 60178.748846 4d216ffc-3699-4b7c-bba7-d706c026edb2 Reverse-engineered motivating website Fixed Amount 8.08 487 1489474.60 3058.469405 57287.484615 7979a1e8-0e76-4532-b128-48d4a9353950 User-friendly fault-tolerant benchmark Percentage 10.51 516 1478417.70 2865.150581 7040

### INVENTORY MANAGEMENT
- For every product, calculate how many copies are sold and how many left?

In [0]:
spark.sql(f"""
            CREATE OR REPLACE TABLE gold_inventory_management
            USING DELTA
            LOCATION '{gold_path}/inventory_management'
            AS
            SELECT 
                p.product_id, p.product_name, p.category, p.in_stock, p.inventory_status,
                COALESCE(SUM(oi.quantity), 0) AS total_quantity_sold,
                p.in_stock - COALESCE(SUM(oi.quantity), 0) AS current_stock,
                CASE
                    WHEN p.in_stock > 0 THEN COALESCE(SUM(oi.quantity), 0) / p.in_stock
                    ELSE 0
                END AS turnover_rate
            FROM silver_db.silver_products p
            LEFT JOIN silver_db.silver_orderLineItems oi 
            ON p.product_id = oi.product_id
            GROUP BY p.product_id, p.product_name, p.category, p.in_stock, p.inventory_status
""")

Out[27]: DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql
SELECT * FROM gold_inventory_management WHERE current_stock < 0

product_id product_name category in_stock inventory_status total_quantity_sold current_stock turnover_rate bba49bdb-3d85-46c2-91f4-df307330d0f3 User-friendly cohesive adapter Jewelry 1 Hot Sellers 29.0 -28.0 29.0 ef1e3662-1b9c-411d-ab94-405ef0322275 Multi-layered even-keeled orchestration Electronics 3 Hot Sellers 31.0 -28.0 10.333333333333334 0c5f5e2e-c8cd-4a7a-8b2a-ff4e0a492b56 Polarized transitional conglomeration Health & Wellness 12 Hot Sellers 29.0 -17.0 2.4166666666666665 251e01ce-379d-4851-8c19-f77995390b12 Object-based dynamic matrix Cosmetics 1 Hot Sellers 46.0 -45.0 46.0 32aef856-3df6-41d9-a95e-15312214edfc Enhanced maximized workforce Clothing 37 Hot Sellers 50.0 -13.0 1.3513513513513513 35355df2-ecea-4dfd-bd03-47a727c43649 Polarized modular migration Baby Products 27 Hot Sellers 76.0 -49.0 2.814814814814815 0d9ef732-21ca-461b-ae19-d6a7ce8d453b Balanced high-level portal Automotive 21 Hot Sellers 43.0 -22.0 2.0476190476190474 66becd57-72a4-4c8f-91ff-be35da317d8e Triple-buffered 24/7 task-force Furniture 14 Hot Sellers 51.0 -37.0 3.642857142857143 c7cdd8ad-7524-428a-aaf5-aac1d2746dd9 Right-sized 24/7 help-desk Cosmetics 27 Hot Sellers 48.0 -21.0 1.7777777777777777 e380055d-a880-4b2f-8fb6-e8f0d8678f69 Stand-alone neutral matrix Clothing 26 Hot Sellers 49.0 -23.0 1.8846153846153846 f21c3468-fe4e-4080-a7b5-2bf3cb2a9211 Compatible dynamic synergy Automotive 4 Hot Sellers 49.0 -45.0 12.25 6df510cc-1eac-4bd8-8d43-d34471744919 Focused content-based encryption Pet Supplies 47 Hot Sellers 51.0 -4.0 1.0851063829787233 7acb806d-eb49-4e2d-bae9-bf20f9763eca User-friendly web-enabled throughput Uncategorized 14 Hot Sellers 21.0 -7.0 1.5 8f290b7f-5d69-4666-9b26-b1d106b96c5b Pre-emptive holistic encoding Food & Beverages 30 Hot Sellers 31.0 -1.0 1.0333333333333334 ea3a4dce-89d3-4ace-a79a-0d74eeecc8ff Down-sized high-level interface Home & Garden 23 Hot Sellers 48.0 -25.0 2.0869565217391304 b1e0d484-9e91-42de-8e6b-6b09826ed75f Proactive reciprocal collaboration Pet Supplies 24 Hot Sellers 51.0 -27.0 2.125 64b864e9-9596-40f6-9df6-8c78f02c6f37 Persistent homogeneous info-mediaries Automotive 31 Hot Sellers 62.0 -31.0 2.0 c088d978-bfa6-463e-8a44-abc7b29ae56d Public-key multi-tasking migration Pet Supplies 33 Hot Sellers 48.0 -15.0 1.4545454545454546 3be26d21-4b16-4c14-bb2b-5efb1ee831de Extended solution-oriented infrastructure Clothing 22 Hot Sellers 46.0 -24.0 2.090909090909091 a9c9f47f-5d9e-4dad-8131-fb50c0edd468 Devolved value-added array Home & Garden 14 Hot Sellers 38.0 -24.0 2.7142857142857144 be096917-f294-4686-8917-90bae4245f85 Exclusive zero-defect benchmark Office Supplies 1 Hot Sellers 12.0 -11.0 12.0 212dab2f-7fa6-49d6-a071-d50198a96bb6 Reactive foreground benchmark Outdoor & Camping 28 Hot Sellers 32.0 -4.0 1.1428571428571428 d3c0ec94-4ffa-404f-a271-378a8b5d7f18 Operative exuding solution Art & Crafts 4 Hot Sellers 19.0 -15.0 4.75 258f65d3-c9ba-4f92-9a5e-d4fff0a79d00 Function-based explicit website Food & Beverages 23 Hot Sellers 31.0 -8.0 1.3478260869565217 8a006251-bb09-4f1d-91f1-94012f1648e3 Multi-tiered uniform archive Home & Garden 7 Hot Sellers 57.0 -50.0 8.142857142857142 34d52c44-3a62-48e8-a72d-1f88b4159df8 Secured tertiary productivity Sports 4 Hot Sellers 22.0 -18.0 5.5 cc782cab-cd82-47bb-8195-281bd6ed3430 Triple-buffered upward-trending info-mediaries Home & Garden 27 Hot Sellers 40.0 -13.0 1.4814814814814814 094c49a3-ab59-45d1-8be2-76e0825f6448 Focused context-sensitive extranet Food & Beverages 4 Hot Sellers 22.0 -18.0 5.5 06121626-d8d2-48e8-9b02-e05b84e28dee Face-to-face reciprocal Graphical User Interface Baby Products 39 Hot Sellers 53.0 -14.0 1.358974358974359 d21fbda7-b697-4554-b02a-e7297dfae059 Virtual 3rdgeneration hardware Outdoor & Camping 23 Hot Sellers 44.0 -21.0 1.9130434782608696 4dd236df-0e9a-4c06-ab80-6802368196f2 Switchable background moratorium Automotive 24 Hot Sellers 33.0 -9.0 1.375 8e990a99-4edd-4b5f-afdc-e859b9e1b579 Re-engineered contextually-based analyzer Automotive 56 Fast Selling 68.

### GOLD STANDARD VIEWS
- SQL views are virtual tables that are defined by a SQL query. 
- They provide a way to simplify complex queries, enhance data security, and present data in a more user-friendly format.

#### Key Characteristics
- Virtual tables: Views don't store data themselves; they display data from other tables.

- Saved queries: Views are essentially saved SQL queries that can be reused.

- Dynamic: The data in a view updates automatically when the underlying tables change.

#### View 1 - Most Spending Customers

In [0]:
%sql

SELECT * FROM gold_db.gold_customer_analytics LIMIT 5

customer_id first_name last_name formatted_phone_number total_orders lifetime_value average_order_value average_days_between_orders ede5f14f-215e-4e11-9fe6-3970e9536c71 Tamara Taylor 395-988-0078 31 74072.82 2389.445806 1.39 07641eba-0251-43bd-8956-99462feec149 David Spence 554-403-2839 20 54315.68 2715.784000 2.2 3df6ac8a-fdaf-41a5-bea7-d4ec49ac0f37 James King 384-298-8302 31 80744.10 2604.648387 1.42 87662bc8-9167-4fbe-bea9-23cdbef84a42 Michael Morgan 145-686-3125 24 56768.55 2365.356250 1.92 aa66c859-e380-4971-ac69-d46717872ca1 Lisa Williamson 764-210-2818 21 68492.71 3261.557619 1.9

In [0]:
# Create Gold Standard Views
spark.sql("""
        CREATE OR REPLACE VIEW gold_db.vw_customer_lifetime_value 
        AS
                SELECT customer_id, 
                        concat(first_name, ' ', last_name) AS full_name,
                        formatted_phone_number,
                        total_orders,
                        lifetime_value,
                        average_order_value,
                        average_days_between_orders
                FROM gold_db.gold_customer_analytics
                ORDER BY lifetime_value DESC
""")


Out[42]: DataFrame[]

In [0]:
%sql

SELECT * FROM gold_db.vw_customer_lifetime_value LIMIT 10

customer_id full_name formatted_phone_number total_orders lifetime_value average_order_value average_days_between_orders 99f320f6-78fc-4c21-b8bc-8ea20957fd7e Kayla Mayer 330-865-7801 36 149267.28 4146.313333 1.22 24402009-a850-40af-ad0f-ff21ae1d0b05 Sean Lane 515-280-0384 42 131971.49 3142.178333 1.02 94b317f4-8d2d-40aa-af6d-712b0b067e69 Nicholas Brown 460-321-7789 38 130699.53 3439.461316 1.16 a364ac44-4b85-4dcf-bdf1-2b19018f12f9 Donald Cantrell 033-219-1815 44 129227.98 2936.999545 1.0 6027a1e8-3d3d-4c8c-9392-4e031aa6fefa Jeffery Gutierrez 473-934-2927 37 128138.20 3463.194595 1.19 68e5975b-631b-4c65-a746-2c809f45aa12 Kari Rogers 580-530-2269 40 127723.33 3193.083250 1.1 2fa15d1d-2a2a-4327-81df-7fbc980c9d06 John Williams 874-597-1299 46 126837.57 2757.338478 1.0 02080226-774e-421f-831e-669806329d28 Tracy Miller 812-499-8333 36 124383.73 3455.103611 1.28 6b057784-9181-4495-87a4-009b74bc98e8 Mary Montgomery 080-904-5255 36 122636.75 3406.576389 1.19 0404cb71-0c32-477c-af99-0b6533a7dc88 Cynthia Klein 271-487-3173 34 122589.94 3605.586471 1.32

#### View 2 - Category-wise Top performing 100 products

In [0]:
%sql
SELECT * FROM gold_db.gold_product_performance LIMIT 5

product_id product_name category price_category total_orders total_quantity_sold total_revenue average_selling_price f97115fd-cd2b-4a27-aca6-4a77c32839f2 Reduced fresh-thinking knowledgebase Electronics Mid-range 8 37.0 2294.37 62.010000 6af6d5d1-b2a5-49be-b192-b3a917ff5b9e Integrated intermediate open architecture Sports Premium 6 21.0 6850.41 326.210000 c238d326-2293-426c-b970-c0b81fbe3d0d Universal clear-thinking attitude Pet Supplies Premium 4 26.0 5182.32 199.320000 6ec442ee-0bb4-487e-9fa3-445cdfbf520d Re-contextualized intangible collaboration Baby Products Premium 4 26.0 9344.92 359.420000 57fae15e-1937-4d48-9c65-c1c18b31f8f4 De-engineered responsive portal Uncategorized Premium 8 52.0 18719.48 359.990000

In [0]:
spark.sql("""
            CREATE OR REPLACE VIEW gold_db.vw_top_performing_categories
            AS
                SELECT category,
                       COUNT(DISTINCT product_id) AS num_products 
                FROM 
                    (
                        SELECT *
                        FROM gold_db.gold_product_performance
                        ORDER BY total_revenue DESC
                        LIMIT 100
                    ) 
                GROUP BY category
                ORDER BY num_products DESC
        """)

Out[47]: DataFrame[]

In [0]:
%sql

SELECT * FROM gold_db.vw_top_performing_categories

category num_products Toys 10 Office Supplies 8 Uncategorized 8 Home & Garden 7 Jewelry 5 Baby Products 5 Food & Beverages 5 Movies 5 Music 5 Health & Wellness 5 Furniture 5 Books 5 Electronics 4 Pet Supplies 4 Sports 4 Clothing 4 Outdoor & Camping 4 Automotive 3 Art & Crafts 2 Cosmetics 2

#### View 3 - Which week day has most number orders placed?

In [0]:
%sql
SELECT * FROM gold_db.gold_order_analytics LIMIT 5

month_name weekday_name total_orders total_revenue average_order_value total_shipping_cost February Friday 1062 3023328.45 2846.83 29169.20 February Monday 1294 3674918.25 2839.97 35588.94 February Saturday 1633 4660716.02 2854.08 45313.23 February Sunday 1631 4622977.44 2834.44 44667.49 February Thursday 1094 3113826.05 2846.28 31568.33

In [0]:
spark.sql("""
            CREATE OR REPLACE VIEW gold_db.vw_weekday_sales_analysis 
            AS
                SELECT weekday_name,
                       SUM(total_orders) AS total_orders_placed,
                       SUM(total_revenue) AS total_revenue_earned,
                       AVG(average_order_value) AS avg_revenue_earned  
                FROM gold_db.gold_order_analytics
                GROUP BY weekday_name
                ORDER BY total_orders_placed DESC
""")

Out[51]: DataFrame[]

In [0]:
%sql
SELECT * FROM gold_db.vw_weekday_sales_analysis

weekday_name total_orders_placed total_revenue_earned avg_revenue_earned Friday 3836 10779331.95 2821.395000 Thursday 3836 10853664.22 2834.490000 Sunday 3826 10705347.56 2802.725000 Wednesday 3814 10355701.11 2704.690000 Saturday 3795 10753563.25 2836.115000 Monday 3532 9959200.18 2823.980000 Tuesday 3327 9403538.29 2827.495000

#### Show tables in silver and gold databases 

In [0]:
# Verify created tables and views
print("Silver Layer Tables:")
display(spark.sql("SHOW TABLES IN silver_db"))

print("Gold Layer Tables and Views:")
display(spark.sql("SHOW TABLES IN gold_db"))

Silver Layer Tables:


database tableName isTemporary silver_db silver_customers false silver_db silver_orderlineitems false silver_db silver_orders false silver_db silver_products false silver_db silver_promotions false

Gold Layer Tables and Views:


database tableName isTemporary gold_db gold_customer_analytics false gold_db gold_inventory_management false gold_db gold_order_analytics false gold_db gold_product_performance false gold_db gold_promotion_effectiveness false gold_db vw_customer_lifetime_value false gold_db vw_sales_trend_analysis false gold_db vw_top_performing_categories false gold_db vw_weekday_sales_analysis false

In [0]:
display(spark.sql(""" SHOW VIEWS FROM gold_db """))

namespace viewName isTemporary isMaterialized gold_db vw_customer_lifetime_value false false gold_db vw_product_performance false false gold_db vw_sales_trend_analysis false false gold_db vw_promotion_effectiveness false false